In [1]:
import sys
import os

# Add the parent folder of 'src' to sys.path
sys.path.append(os.path.abspath(os.path.join(os.path.dirname(""), '..', 'src')))

In [2]:
%pip install whoosh
%pip install ir_datasets
%pip install ir-measures
%pip install pytrec_eval
%pip install gensim
%pip install nltk
%pip install wordcloud

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [3]:

import ir_datasets

from pagerank import build_graph, undirected_page_rank, improved_page_rank
from delivery1 import indexing, ranking

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/joaquimlbacao/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/joaquimlbacao/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [4]:
# extract datatset
dataset = ir_datasets.load("cord19/trec-covid")
for doc in dataset.docs_iter():
    doc # namedtuple<doc_id, title, doi, date, abstract, body> body: Tuple[title, text]

# qrel  namedtuple<query_id, doc_id, relevance, iteration
# query namedtuple<query_id, title, description, narrative>

qrels = {}
for qrel in dataset.qrels_iter():
    query_id = str(qrel.query_id)
    doc_id = str(qrel.doc_id)
    relevance = qrel.relevance

    if query_id not in qrels:
        qrels[query_id] = {}

    qrels[query_id][doc_id] = relevance

queries = {str(query.query_id): query.title for query in dataset.queries_iter()}

In [ ]:
ixmf_language = indexing(dataset, preprocessing="language")

In [6]:
from whoosh import index

results_bm25f = {}
results_pagerank05 = {}
results_pagerank07 = {}
results_pagerank09 = {}
results_pagerank_improved = {}
ix = index.open_dir(f"indexmf_language_dir")


for query in queries.items():
    retrieved_results = ranking(ix, query, model="bm25f", top_k=1000)
    results_bm25f[query[0]] = retrieved_results

    retrieved_set = set(retrieved_results)

    # as list
    docs_to_build = []
    # as dictionary with prior values
    doc_info = {}

    for doc in dataset.docs_iter():
        if doc.doc_id in retrieved_set:
            docs_to_build.append(doc)
            doc_info[doc.doc_id] = (doc, retrieved_results[doc.doc_id])

    
    page_rank05 = undirected_page_rank(docs_to_build, threshold=0.5)
    page_rank07 = undirected_page_rank(docs_to_build, threshold=0.7)
    page_rank09 = undirected_page_rank(docs_to_build, threshold=0.9)
    page_rank_improved = improved_page_rank(doc_info, threshold=0.9)

    results_pagerank05[query[0]] = page_rank05
    results_pagerank07[query[0]] = page_rank07
    results_pagerank09[query[0]] = page_rank09
    results_pagerank_improved[query[0]] = page_rank_improved

    print("query:", query[0])
    print("- page rank threshold 0.5:", page_rank05)
    print("- page rank threshold 0.7:", page_rank07)
    print("- page rank threshold 0.9:", page_rank09)
    print("- improved page rank:", page_rank_improved)

query: 1
- page rank threshold 0.5: {'66hhozo2': 0.0023929393550564965, 'xcsl2evz': 0.0015793687535198887, 'kkga96h9': 0.001466952984948719, 'zbmsaj8s': 0.001466952984948719, '3lqk5od5': 0.0014593299118749279, 'jwopq9jl': 0.0014593299118749279, '4almssg6': 0.0014202885329926607, 'r25kuerc': 0.0012982540730857347, 'bim76jna': 0.0012982540730857347, 'mw0wb8a8': 0.0012440156502392776, '4bdusuqq': 0.0011984513881209806, '42wv7zl6': 0.0011827667889840723, 'vimbhox4': 0.0011289100913810784, 'c4vk23a6': 0.0011289100913810784, 'uhq8tp4u': 0.0011286207087184653, '69fmtury': 0.0011286207087184653, 'wlmu65vm': 0.0010595857839718916, '75dwpw6l': 0.0010595857839718916, 'x3sb1o4u': 0.0010426438451045846, 'u7zze0dk': 0.0010426438451045846, '2054zqw9': 0.0010426438451045846, '8y24j34j': 0.0010000063442879856, 'ctb7u1zy': 0.0010000063442879856, 'mx1w3l0t': 0.0010000063442879856, '66xk0qqq': 0.0010000063442879856, '0wm6u10a': 0.0010000063442879856, 'rxrlbw60': 0.0010000063442879856, 'tgo8wnz8': 0.001000

In [7]:
import pytrec_eval

metrics = {'map_cut.1000', 'ndcg_cut.1000', 'P_10', 'ndcg_cut.10'}

def evaluate_results(results):
    evaluator = pytrec_eval.RelevanceEvaluator(qrels, metrics)
    return evaluator.evaluate(results)

scores_bm25f = evaluate_results(results_bm25f)
scores_pagerank05 = evaluate_results(results_pagerank05)
scores_pagerank07 = evaluate_results(results_pagerank07)
scores_pagerank09 = evaluate_results(results_pagerank09)
scores_pagerank_improved = evaluate_results(results_pagerank_improved)

final_scores_bm25f = {metric: sum([v[metric] for v in scores_bm25f.values()]) / len(scores_bm25f) for metric in scores_bm25f[list(scores_bm25f.keys())[0]]}
final_scores_pagerank05 = {metric: sum([v[metric] for v in scores_pagerank05.values()]) / len(scores_pagerank05) for metric in scores_pagerank05[list(scores_pagerank05.keys())[0]]}
final_scores_pagerank07 = {metric: sum([v[metric] for v in scores_pagerank07.values()]) / len(scores_pagerank07) for metric in scores_pagerank07[list(scores_pagerank07.keys())[0]]}
final_scores_pagerank09 = {metric: sum([v[metric] for v in scores_pagerank09.values()]) / len(scores_pagerank09) for metric in scores_pagerank09[list(scores_pagerank09.keys())[0]]}
final_scores_pagerank_improved = {metric: sum([v[metric] for v in scores_pagerank_improved.values()]) / len(scores_pagerank_improved) for metric in scores_pagerank_improved[list(scores_pagerank_improved.keys())[0]]}


print("\nBM25F Evaluation:")
for metric, score in final_scores_bm25f.items():
    print(f"{metric}: {score:.4f}")

print("\nPageRank Evaluation for Threshold = 0.5:")
for metric, score in final_scores_pagerank05.items():
    print(f"{metric}: {score:.4f}")

print("\nPageRank Evaluation for Threshold = 0.7:")
for metric, score in final_scores_pagerank07.items():
    print(f"{metric}: {score:.4f}")

print("\nPageRank Evaluation for Threshold = 0.9:")
for metric, score in final_scores_pagerank09.items():
    print(f"{metric}: {score:.4f}")

print("\nImproved PageRank Evaluation:")
for metric, score in final_scores_pagerank_improved.items():
    print(f"{metric}: {score:.4f}")


BM25F Evaluation:
P_10: 0.7280
ndcg_cut_10: 0.6765
ndcg_cut_1000: 0.3975
map_cut_1000: 0.2069

PageRank Evaluation for Threshold = 0.5:
P_10: 0.2180
ndcg_cut_10: 0.1686
ndcg_cut_1000: 0.3166
map_cut_1000: 0.0955

PageRank Evaluation for Threshold = 0.7:
P_10: 0.2720
ndcg_cut_10: 0.2353
ndcg_cut_1000: 0.3245
map_cut_1000: 0.1004

PageRank Evaluation for Threshold = 0.9:
P_10: 0.2680
ndcg_cut_10: 0.2471
ndcg_cut_1000: 0.3252
map_cut_1000: 0.1001

Improved PageRank Evaluation:
P_10: 0.2840
ndcg_cut_10: 0.2366
ndcg_cut_1000: 0.3246
map_cut_1000: 0.1019
